In [1]:
import os
if "ntbk" in os.getcwd():
    os.chdir("..")
print(os.getcwd())

import sys
sys.path.append(os.path.join(os.getcwd(), "otgnn"))


%load_ext autoreload
%autoreload 2

from otgnn.models import GCN
from otgnn.graph import MolGraph
from otgnn.utils import save_model, load_model

from mol_opt.mol_opt import MolOpt
from mol_opt.data_mol_opt import MolOptDataset
from mol_opt.data_mol_opt import get_loader
from mol_opt.arguments import get_args
from mol_opt.train_mol_opt import main, get_latest_model
from mol_opt.ot_utils import compute_barycenter

from rdkit.Chem import MolFromSmiles

import torch
import numpy as np
import time
import torch.nn.functional as F

/home/octav/gitrepos/tum-thesis


In [2]:
model_type = "deepsets"
sys.argv = ["", "-cuda", "-model_type", model_type]
args = get_args()
outdir_suffix = "dev4"
args.n_epochs = 20000 
args.init_model = "{}-attention-sink5-test1".format(model_type)
# args.init_model = "{}-test1".format(model_type)
args.init_decoder_model = "{}_decode".format(args.init_model)
args.output_dir = "mol_opt/output_{}/{}".format(outdir_suffix, args.init_model)
args.tb_logs_dir = "mol_opt/logs_{}/{}".format(outdir_suffix, args.init_model)
args.batch_size = 50 

args.penalty_gumbel = False 

args.scale_lambdas = True
args.connectivity = True 
args.valency = True 
args.euler_characteristic_penalty = True
args.conn_lambda_start = 0.001
args.conn_lambda_end = 3
args.conn_lambda_epochs_start = 4001
args.conn_lambda_epochs_end = 12000
args.valency_lambda_start = 0.001
args.valency_lambda_end = 5
args.valency_lambda_epochs_start = 4001
args.valency_lambda_epochs_end = 12000
args.euler_lambda_start = 0.001 
args.euler_lambda_end = 2 
args.euler_lambda_epochs_start = 4001
args.euler_lambda_epochs_end = 12000
args.tau_start = 1
args.tau_end = 0.01
args.tau_epochs_start = 1
args.tau_epochs_end = 12000

args.cross_att_use = True
args.cross_att_random = False
args.cross_att_n_sinkhorn = 5
# args.morgan_bits = 1024

args.conn_penalty_function = "capped_logdet" 

print(args, '\n')

Namespace(N_transformer=6, agg_func='sum', batch_norm=False, batch_size=50, conn_lambda_end=3, conn_lambda_epochs_end=12000, conn_lambda_epochs_start=4001, conn_lambda_start=0.001, conn_penalty_function='capped_logdet', connectivity=True, connectivity_hard=False, cross_att_dim=150, cross_att_n_sinkhorn=5, cross_att_random=False, cross_att_use=True, cuda=True, device='cuda:0', dim_tangent_space=40, dropout_ffn=0.0, dropout_gcn=0.0, dropout_transformer=0.1, euler_characteristic_penalty=True, euler_lambda_end=2, euler_lambda_epochs_end=12000, euler_lambda_epochs_start=4001, euler_lambda_start=0.001, ffn_activation='LeakyReLU', init_decoder_model='deepsets-attention-sink5-test1_decode', init_model='deepsets-attention-sink5-test1', linear_out=False, max_num_atoms=70, model_type='deepsets', morgan_bits=0, n_epochs=20000, n_ffn_hidden=100, n_ffn_transformer=100, n_heads_transformer=10, n_hidden=200, n_labels=1, n_layers=5, one_batch_train=False, ot_solver='emd', output_dir='mol_opt/output_dev

In [3]:
# train_data_loader = get_loader("iclr19-graph2graph/data/qed", "train_pairs", args.batch_size, same_number_atoms = True)
# train_data_loader = get_loader("molgen/data/chembl50", "train", args.batch_size, same_number_atoms = True)
# val_data_loader = get_loader("iclr19-graph2graph/data/qed", "valid", 36, False)

train_data_loader = get_loader("molgen/data/chembl50", "train", args.batch_size, same_number_atoms = True)
# val_data_loader = get_loader("molgen/data/chembl50", "val_split", args.batch_size, same_number_atoms = True)
val_data_loader = None

In [4]:
molopt, molopt_decoder = main(args, train_data_loader = train_data_loader, val_data_loader = val_data_loader)

No model deepsets-attention-sink5-test1 found in mol_opt/output_dev4/deepsets-attention-sink5-test1! Starting from scratch.
Penalty params: tau=1.00000 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=-1 mode=[0 0 0] conn=True val=True euler=True
Epoch: 1


/home/octav/gitrepos/tum-thesis/otgnn/models/gromov_modules.py:398: UserWarning: Implicit dimension choice for log_softmax has been deprecated. Change the call to include dim=X as an argument.
  nce_reg = torch.nn.LogSoftmax()(torch.stack(all_nce_dists))[0]


Losses Batch 0, train
 fgw:5259.1568750
 conn_penalty:0.0000000
 val_penalty:684.7399219
 euler_penalty:200.0378906
 total:5260.0406250
Penalty params: tau=1.00000 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=1 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=1.00000 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=1 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 1, train
 fgw:5259.1568750
 conn_penalty:0.0000000
 val_penalty:684.7399219
 euler_penalty:200.0378906
 total:5260.0406250
Epoch duration: 5.471258878707886
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-sink5-test1/model_deepsets-attention-sink5-test1_1
Epoch: 2
Losses Batch 0, train
 fgw:3183.9296875
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:3183.9296875
Penalty params: tau=0.99962 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=2 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.99962 conn_l=0.00

Losses Batch 0, train
 fgw:455.3789453
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:455.3789453
Penalty params: tau=0.99541 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=13 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.99541 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=13 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 13, train
 fgw:455.3789453
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:455.3789453
Epoch duration: 0.8033804893493652
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-sink5-test1/model_deepsets-attention-sink5-test1_13
Epoch: 14
Losses Batch 0, train
 fgw:456.6320313
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:456.6320313
Penalty params: tau=0.99502 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=14 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.99502 conn_l=0.00100 val

Losses Batch 0, train
 fgw:379.0322266
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:379.0322266
Penalty params: tau=0.99083 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=25 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.99083 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=25 mode=[0 0 0] conn=False val=False euler=False
Losses Epoch 25, train
 fgw:379.0322266
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:379.0322266
Epoch duration: 0.8370182514190674
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-sink5-test1/model_deepsets-attention-sink5-test1_25
Epoch: 26
Losses Batch 0, train
 fgw:374.7848828
 conn_penalty:0.0000000
 val_penalty:0.0000000
 euler_penalty:0.0000000
 total:374.7848828
Penalty params: tau=0.99045 conn_l=0.00100 val_l=0.00100 euler_l=0.00100 epoch=26 mode=[0 0 0] conn=False val=False euler=False
Penalty params: tau=0.99045 conn_l=0.00100 val

...

Losses Batch 0, train
 fgw:259.7549609
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:265.0451953
Penalty params: tau=0.06396 conn_l=0.02374 val_l=0.02906 euler_l=0.02022 epoch=7165 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.06396 conn_l=0.02374 val_l=0.02906 euler_l=0.02022 epoch=7165 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7165, train
 fgw:259.7549609
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:265.0451953
Epoch duration: 4.583987712860107
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-sink5-test1/model_deepsets-attention-sink5-test1_7165
Epoch: 7166
Losses Batch 0, train
 fgw:259.7520117
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:265.0475391
Penalty params: tau=0.06393 conn_l=0.02377 val_l=0.02909 euler_l=0.02024 epoch=7166 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.06393 conn

Losses Batch 0, train
 fgw:259.7154102
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:265.0698047
Penalty params: tau=0.06366 conn_l=0.02403 val_l=0.02943 euler_l=0.02046 epoch=7177 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.06366 conn_l=0.02403 val_l=0.02943 euler_l=0.02046 epoch=7177 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7177, train
 fgw:259.7154102
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:265.0698047
Epoch duration: 4.573037147521973
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-sink5-test1/model_deepsets-attention-sink5-test1_7177
Epoch: 7178
Losses Batch 0, train
 fgw:259.7114844
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:265.0712500
Penalty params: tau=0.06364 conn_l=0.02405 val_l=0.02947 euler_l=0.02048 epoch=7178 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.06364 conn

Losses Batch 0, train
 fgw:259.6668945
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:265.0862500
Penalty params: tau=0.06337 conn_l=0.02432 val_l=0.02981 euler_l=0.02069 epoch=7189 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.06337 conn_l=0.02432 val_l=0.02981 euler_l=0.02069 epoch=7189 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7189, train
 fgw:259.6668945
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:265.0862500
Epoch duration: 4.900964975357056
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-sink5-test1/model_deepsets-attention-sink5-test1_7189
Epoch: 7190
Losses Batch 0, train
 fgw:259.6639453
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:265.0887500
Penalty params: tau=0.06335 conn_l=0.02435 val_l=0.02984 euler_l=0.02071 epoch=7190 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.06335 conn

Losses Batch 0, train
 fgw:259.6319531
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:265.1170508
Penalty params: tau=0.06308 conn_l=0.02461 val_l=0.03020 euler_l=0.02093 epoch=7201 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.06308 conn_l=0.02461 val_l=0.03020 euler_l=0.02093 epoch=7201 mode=[1 1 1] conn=True val=True euler=True
Losses Epoch 7201, train
 fgw:259.6319531
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:265.1170508
Epoch duration: 4.689262628555298
Saving model, do not interrupt...
Saved at mol_opt/output_dev4/deepsets-attention-sink5-test1/model_deepsets-attention-sink5-test1_7201
Epoch: 7202
Losses Batch 0, train
 fgw:259.6291211
 conn_penalty:176.1400586
 val_penalty:23.0000000
 euler_penalty:22.0000000
 total:265.1197266
Penalty params: tau=0.06306 conn_l=0.02464 val_l=0.03023 euler_l=0.02095 epoch=7202 mode=[1 1 1] conn=True val=True euler=True
Penalty params: tau=0.06306 conn

KeyboardInterrupt: 